In [1]:
import pandas as pd
df = pd.read_csv('df_no_images.csv')

In [2]:
df

Unnamed: 0  user_id                     location      age        isbn  \
0          835924    88984       sydney, nsw, australia  34.7439  0395717566   
1           16726   259066      oakley, california, usa  56.0000  0316776963   
2          940754   271705        atlanta, georgia, usa  25.0000  0192834371   
3          965187   186570       rantoul, illinois, usa  28.0000  0380758636   
4          277519   255651        urbana, illinois, usa  34.7439  0679451145   
...           ...      ...                          ...      ...         ...   
99964      425513   193898  paradise, pennsylvania, usa  34.7439  0380726246   
99965      839275   257198    edmonton, alberta, canada  34.0000  0061054372   
99966      759782   105374     montreal, quebec, canada  25.0000  0192876791   
99967      727870   189334      ottawa, ontario, canada  49.0000  0345303075   
99968      194765   265115       vista, california, usa  34.7439  0440509238   

       rating                                         book_title  \
0           0             the best american essays 1996 (serial)   
1           9                             me talk pretty one day   
2           0  the communist manifesto (oxford world's classics)   
3           0                                    hint of rapture   
4           0                       the island of the colorblind   
...       ...                                                ...   
99964       0  prayers for the dead : a peter decker/rina laz...   
99965       7    the unauthorized history of trek (harper prism)   
99966       0                                paul (past masters)   
99967      10  white gold wielder (the second chronicles of t...   
99968       0                                         spin cycle   

                book_author  year_of_publication  \
0          Geoffrey C. Ward               1996.0   
1             David Sedaris               2001.0   
2                 Karl Marx               1998.0   
3             Miriam Minger               1990.0   
4           Oliver W. Sacks               1997.0   
...                     ...                  ...   
99964        Faye Kellerman               1997.0   
99965        James Van Hise               1995.0   
99966         E. P. Sanders               1991.0   
99967  Stephen R. Donaldson               1983.0   
99968          SUE MARGOLIS               2001.0   

                                publisher  ... Language              Category  \
0                           Mariner Books  ...       en  literary collections   
1                          Back Bay Books  ...        9                     9   
2                 Oxford University Press  ...       en            philosophy   
3      Harper Mass Market Paperbacks (Mm)  ...        9                     9   
4                        Random House Inc  ...       en               science   
...                                   ...  ...      ...                   ...   
99964                                Avon  ...       en               fiction   
99965  Harper Mass Market Paperbacks (Mm)  ...       en       performing arts   
99966             Oxford University Press  ...       en               history   
99967                    Ballantine Books  ...        9                     9   
99968                               Delta  ...       en               fiction   

           city         state    country Category_frequency  \
0        sydney           nsw  australia               1289   
1        oakley    california        usa             386696   
2       atlanta       georgia        usa               1719   
3       rantoul      illinois        usa             386696   
4        urbana      illinois        usa               2069   
...         ...           ...        ...                ...   
99964  paradise  pennsylvania        usa             368034   
99965  edmonton       alberta     canada               1483   
99966  montreal        quebec     canada               7855   
9

In [3]:

# Gereksiz sütunları temizleyin ve veri setini hazırlayın
df = df[['user_id', 'isbn', 'rating', 'book_title', 'book_author', 'year_of_publication', 'publisher', 'Language', 'Category', 'city', 'state', 'country']]
df.dropna(subset=['book_title', 'book_author', 'Category', 'city', 'state', 'country'], inplace=True)
df['Category'] = df['Category'].str.replace(r"[^\w\s]", "", regex=True)

/var/folders/l9/2zvzfc7n727dpbzc925bm4w00000gn/T/ipykernel_4114/1577746044.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.dropna(subset=['book_title', 'book_author', 'Category', 'city', 'state', 'country'], inplace=True)
/var/folders/l9/2zvzfc7n727dpbzc925bm4w00000gn/T/ipykernel_4114/1577746044.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Category'] = df['Category'].str.replace(r"[^\w\s]", "", regex=True)


In [4]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Kitap başlıkları ve yazarlar için TF-IDF vektörizasyonu
tfidf_title = TfidfVectorizer(stop_words='english')
tfidf_author = TfidfVectorizer(stop_words='english')

tfidf_title_matrix = tfidf_title.fit_transform(df['book_title'])
tfidf_author_matrix = tfidf_author.fit_transform(df['book_author'])

# Kategoriler için birleştirme ve vektörizasyon
df['combined_features'] = df['book_title'] + ' ' + df['book_author'] + ' ' + df['Category']
tfidf_features = TfidfVectorizer(stop_words='english')
tfidf_matrix = tfidf_features.fit_transform(df['combined_features'])

/var/folders/l9/2zvzfc7n727dpbzc925bm4w00000gn/T/ipykernel_4114/3220608094.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['combined_features'] = df['book_title'] + ' ' + df['book_author'] + ' ' + df['Category']


In [5]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

def get_recommendations(book_title, tfidf_matrix, df):
    idx = df[df['book_title'] == book_title].index[0]
    cosine_sim = cosine_similarity(tfidf_matrix[idx], tfidf_matrix).flatten()
    indices = np.argsort(cosine_sim)[::-1]
    return df['book_title'].iloc[indices].values

# Örnek kullanım
recommendations = get_recommendations('the best american essays 1996 (serial)', tfidf_matrix, df)
print(recommendations)

['the best american essays 1996 (serial)' 'the best american essays, 1992'
 'how to be alone: essays' ...
 "the book of ruth (oprah's book club (paperback))" 'the cosmic clues'
 'the day after tomorrow']


In [6]:
from sklearn.metrics.pairwise import cosine_similarity

# Kullanıcı ve kitap matrisi oluşturma
user_book_matrix = df.pivot_table(index='user_id', columns='book_title', values='rating')
user_book_matrix = user_book_matrix.fillna(0)

# Kullanıcı benzerlik matrisini hesaplama
user_similarity = cosine_similarity(user_book_matrix)
user_similarity_df = pd.DataFrame(user_similarity, index=user_book_matrix.index, columns=user_book_matrix.index)

def get_user_recommendations(user_id, user_book_matrix, user_similarity_df):
    similar_users = user_similarity_df[user_id].sort_values(ascending=False).index[1:6]
    similar_users_ratings = user_book_matrix.loc[similar_users].mean()
    user_ratings = user_book_matrix.loc[user_id]
    recommendations = similar_users_ratings[user_ratings == 0].sort_values(ascending=False)
    return recommendations.index.tolist()

# Örnek kullanım
user_recommendations = get_user_recommendations(88984, user_book_matrix, user_similarity_df)
print(user_recommendations)

['a prayer for owen meany', '!yo!', 'solitaire mystery', 'soldiers spys (men at war (paperback pocket))', 'sole survivor', 'sole survivor : children who kill their families', 'solea', 'soledad: a novel', 'soleil en solde', "solid answers: america's foremost family counselor responds to tough questions facing today's families", 'solid state physics', 'solitaire', 'solitaire for 2', 'solitary soldier (a colby agency case) (harlequin intrigue, no. 646)', 'soldiers of fortune', 'solo', 'solo variations', 'soloalbum.', 'soloalbum: roman (kiwi)', 'solomon the supersonic salamander: telling the truth (the wisdom series, no 2)', 'solstice: a novel', "solve your child's sleep problems", "somberman's actie", 'some came running', 'some can whistle', 'soldiers of paradise', "soldier's heart : being the story of the enlistment and due service of the boy charley goddard in the first minnesota volunteers", "some days there's pie", 'sola come un gambo di sedano', 'soft!', 'softball practice (hello rea

In [7]:
def hybrid_recommendations(user_id, book_title, tfidf_matrix, df, user_book_matrix, user_similarity_df):
    # Content-Based Filtering sonuçları
    cbf_recommendations = get_recommendations(book_title, tfidf_matrix, df)
    
    # Collaborative Filtering sonuçları
    cf_recommendations = get_user_recommendations(user_id, user_book_matrix, user_similarity_df)
    
    # Sonuçları birleştirme
    combined_recommendations = list(set(cbf_recommendations) | set(cf_recommendations))
    return combined_recommendations

# Örnek kullanım
hybrid_recs = hybrid_recommendations(88984, 'the best american essays 1996 (serial)', tfidf_matrix, df, user_book_matrix, user_similarity_df)
print(hybrid_recs)

['with good reason: an introduction to informal fallacies', 'a test of wills (inspector ian rutledge mysteries (paperback))', 'lost girls', 'a regency christmas: five stories', 'patchwork math 2 (grades 4-6)', 'diary of a fat housewife:a true story of humor, heart- break and hope', 'tales of the american west: the best of spur award-winning authors', 'durable fire', 'valley of the dolls: a novel', 'through a dark mist', 'no place like home (holiday classics)', 'le jour des fourmis: roman', 'now in november', 'little miss somersault', "the devil's alternative", "custard's last stand: a pennsylvania dutch mystery with recipes (magdalena yoder mysteries)", 'slapstick or lonesome no more!', 'the keep', 'jack and the beanstalk', 'saul and patsy : a novel', 'love is a racket', 'emil und die detektive / emil und die drei zwillinge. ( ab 10 j.).', 'wrong kind of girl (sweet valley high series no. 10)', 'the clinic', 'balance point (star wars: the new jedi order, book 6)', 'doctor sax: faust pa

In [9]:
import ipywidgets as widgets
from IPython.display import display

# Widget'lar oluşturun
user_id_widget = widgets.IntText(
    description='User ID:',
    placeholder='Enter user ID'
)
book_title_widget = widgets.Text(
    description='Book Title:',
    placeholder='Enter book title'
)
recommend_button = widgets.Button(description='Get Recommendations')

# Öneri fonksiyonunu tanımlayın
def on_button_click(b):
    user_id = user_id_widget.value
    book_title = book_title_widget.value
    recommendations = hybrid_recommendations(user_id, book_title, tfidf_matrix, df, user_book_matrix, user_similarity_df)
    if recommendations:
        print("Recommendations:")
        for book in recommendations[:10]:
            print(book)
    else:
        print("No recommendations found.")

# Düğmeye tıklama olayını bağlayın
recommend_button.on_click(on_button_click)

# Widget'ları gösterin
display(user_id_widget, book_title_widget, recommend_button)

IntText(value=0, description='User ID:')

Text(value='', description='Book Title:', placeholder='Enter book title')

Button(description='Get Recommendations', style=ButtonStyle())

Recommendations:
with good reason: an introduction to informal fallacies
a test of wills (inspector ian rutledge mysteries (paperback))
lost girls
a regency christmas: five stories
patchwork math 2 (grades 4-6)
diary of a fat housewife:a true story of humor, heart- break and hope
tales of the american west: the best of spur award-winning authors
durable fire
valley of the dolls: a novel
through a dark mist


In [10]:
df

user_id        isbn  rating  \
0        88984  0395717566       0   
1       259066  0316776963       9   
2       271705  0192834371       0   
3       186570  0380758636       0   
4       255651  0679451145       0   
...        ...         ...     ...   
99964   193898  0380726246       0   
99965   257198  0061054372       7   
99966   105374  0192876791       0   
99967   189334  0345303075      10   
99968   265115  0440509238       0   

                                              book_title  \
0                 the best american essays 1996 (serial)   
1                                 me talk pretty one day   
2      the communist manifesto (oxford world's classics)   
3                                        hint of rapture   
4                           the island of the colorblind   
...                                                  ...   
99964  prayers for the dead : a peter decker/rina laz...   
99965    the unauthorized history of trek (harper prism)   
99966                                paul (past masters)   
99967  white gold wielder (the second chronicles of t...   
99968                                         spin cycle   

                book_author  year_of_publication  \
0          Geoffrey C. Ward               1996.0   
1             David Sedaris               2001.0   
2                 Karl Marx               1998.0   
3             Miriam Minger               1990.0   
4           Oliver W. Sacks               1997.0   
...                     ...                  ...   
99964        Faye Kellerman               1997.0   
99965        James Van Hise               1995.0   
99966         E. P. Sanders               1991.0   
99967  Stephen R. Donaldson               1983.0   
99968          SUE MARGOLIS               2001.0   

                                publisher Language              Category  \
0                           Mariner Books       en  literary collections   
1                          Back Bay Books        9                     9   
2                 Oxford University Press       en            philosophy   
3      Harper Mass Market Paperbacks (Mm)        9                     9   
4                        Random House Inc       en               science   
...                                   ...      ...                   ...   
99964                                Avon       en               fiction   
99965  Harper Mass Market Paperbacks (Mm)       en       performing arts   
99966             Oxford University Press       en               history   
99967                    Ballantine Books        9                     9   
99968                               Delta       en               fiction   

           city         state    country  \
0        sydney           nsw  australia   
1        oakley    california        usa   
2       atlanta       georgia        usa   
3       rantoul      illinois        usa   
4        urbana      illinois        usa   
...         ...           ...        ...   
99964  paradise  pennsylvania        usa   
99965  edmonton       alberta     canada   
99966  montreal        quebec     canada   
99967    ottawa       ontario     canada   
99968     vista    california        usa   

                                       combined_features  
0      the best american essays 1996 (serial) Geoffre...  
1                 me talk pretty one day David Sedaris 9  
2      the communist manifesto (oxford world's classi...  
3                        hint of rapture Miriam Minger 9  
4      the island of the colorblind Oliver W. Sacks s...  
...                                                  ...  
99964  prayers for the dead : a peter decker/rina laz...  
99965  the unauthorized history of trek (harper prism...  
99966          paul (past masters) E. P. Sanders history  
99967  white gold wielder (the second chronicles of t...  
99968                    spin cycle SUE MARGOLIS fiction  

[99629 rows x 13 columns]

In [ ]:
# created by azad halhalli
